In [1]:
from subprocess import Popen, PIPE, CalledProcessError
import re
import platform
import shutil
import os.path
import fileinput
import ipywidgets as widgets
from io import BytesIO
import xml.etree.cElementTree as ET
from functools import partial
import time
import getpass
from encrypt import decryptCredentials,decryptString
import gmaps
import psycopg2 as db
from psycopg2.extensions import AsIs
import requests
from bs4 import BeautifulSoup
from bs4 import SoupStrainer
from urllib.parse import urljoin

options = {'stdout': PIPE, 'stderr': PIPE, 'bufsize' : 1, 'universal_newlines' : True, 'shell' : False}
if (platform.system() == 'Windows'):
    options['shell'] = True
    #Packages required to generate ssh keys in windows
    from cryptography.hazmat.primitives import serialization as crypto_serialization
    from cryptography.hazmat.primitives.asymmetric import rsa
    from cryptography.hazmat.backends import default_backend as crypto_default_backend

def callPopen(cmd):
    print(cmd)
    with Popen(cmd.split(),**options) as p:
        for line in p.stdout:
            print(line, end='')
        for line in p.stderr:
            print(line, end='')
        if p.returncode != (0 or None):
            raise CalledProcessError(p.returncode, p.args)

def isInstance(name):
    instanceExists=False
    ip=''
    with Popen('gcloud compute instances list'.split(),**options) as p:
        for line in p.stdout:
            if re.match('^{}'.format(name), line):
                instanceExists=True
                ip = line.strip().split()
                ip = ip[4]
        for line in p.stderr:
            print(line, end='')
        if p.returncode != (0 or None):
            raise CalledProcessError(p.returncode, p.args)
        return(instanceExists,ip)
    
            
def text_prepender(filename, text):
    with open(filename, 'r+') as f:
        content = f.read()
        f.seek(0, 0)
        f.write(text.rstrip('\r\n') + content)

def replace(file,pattern,replace):
    fileinput.close()
    for line in fileinput.input(file, inplace=True):
        print( re.sub(pattern,
                      replace,
                      line.rstrip()
                      ) 
             )
        
if (platform.system() == 'Windows'):
    def generateSSHKey(username,savePath):
        key = rsa.generate_private_key(
            backend=crypto_default_backend(),
            public_exponent=65537,
            key_size=2048
            )
        private_key = key.private_bytes(
            crypto_serialization.Encoding.PEM,
            crypto_serialization.PrivateFormat.TraditionalOpenSSL,
            crypto_serialization.NoEncryption()
            )
        public_key = key.public_key().public_bytes(
            crypto_serialization.Encoding.OpenSSH,
            crypto_serialization.PublicFormat.OpenSSH
            )
        public_file = os.path.join(savePath,username + '.pub')
        private_file = os.path.join(savePath,username)
        text_file = open(public_file, "w")
        text_file.write(public_key.decode('utf-8') + ' ' + username)
        text_file.close()
        text_file = open(private_file, "w")
        text_file.write(private_key.decode('utf-8'))
        text_file.close()
        print('Successfully created key pair')
            
if (platform.system() == 'Linux'):
    def generateSSHKey(username,savePath):
        p = Popen("echo 'yes' | ssh-keygen -t rsa -f {0}/{1} -C {1} -N '' ".format(savePath,username),
              stdout=PIPE,
              shell=True,
              stderr=PIPE
               )
        print(p.communicate())   

# Getting data from metno thredds servers
## Creating a virtual machine with the fimex utility

In [2]:
instanceName = 'fimex-fast'
username = 'jose-luis'

createInstance = '''
gcloud compute instances create {} 
--zone europe-west3-a 
--image-family ubuntu-1604-lts 
--image-project ubuntu-os-cloud 
--machine-type n1-standard-8 
--scopes default,storage-rw
'''
#--boot-disk-size 200GB \
#--machine-type n1-highcpu-32  n1-standard-2\
deleteInstance = '''\
gcloud compute instances delete {} \
--zone europe-west-3a \
'''

listInstances = '''gcloud compute instances list'''

addSSHKeys = '''gcloud compute instances add-metadata {} --zone europe-west3-a --metadata-from-file ssh-keys={}'''

if (platform.system() == 'Linux'):
    keyDir = ('/home/jose-luis/.ssh/fimexKeys')

if (platform.system() == 'Windows'):
    keyDir = ('c:/Users/jose_luis_guerrero/fimexKeys')
    

ip=''
instanceExists,ip = isInstance(instanceName)

if instanceExists:
    print('Instance {} is {}'.format(instanceName,ip) )

isStarted = False
if instanceExists and ip == 'TERMINATED' :
    callPopen('gcloud compute instances start {} --zone europe-west3-a'.format(instanceName))
    instanceExists,ip = isInstance(instanceName)
    isStarted = True
    print("Machine started and ip is {}".format(ip))

wasCreated=False
if not instanceExists and not isStarted:
    callPopen(createInstance.format(instanceName))
    wasCreated=True
    if os.path.exists(keyDir):
        shutil.rmtree(keyDir)
    os.mkdir(keyDir)
    generateSSHKey(username,keyDir)
    keyFile = os.path.join(keyDir,username + '.pub')
    text_prepender('{}/{}.pub'.format(keyDir,username), '{}:'.format(username) )
    callPopen(addSSHKeys.format(instanceName,keyDir + '/{}.pub'.format(username)))
    #callPopen('sed -i s/^{0}:// {1}/{0}.pub'.format(username,keyDir))
    replace(keyFile,"^{}:".format(username),"")
    ip=isInstance(instanceName)[1]
        #callPopen('chmod 400 {}'.format(keyDir))
        
print("The ip of {} is {}".format(instanceName,ip))


gcloud compute instances create fimex-fast 
--zone europe-west3-a 
--image-family ubuntu-1604-lts 
--image-project ubuntu-os-cloud 
--machine-type n1-standard-8 
--scopes default,storage-rw

NAME        ZONE            MACHINE_TYPE   PREEMPTIBLE  INTERNAL_IP  EXTERNAL_IP     STATUS
fimex-fast  europe-west3-a  n1-standard-8               10.156.0.9   35.234.102.160  RUNNING
Created [https://www.googleapis.com/compute/v1/projects/nivacatchment/zones/europe-west3-a/instances/fimex-fast].
(b"Generating public/private rsa key pair.\nYour identification has been saved in /home/jose-luis/.ssh/fimexKeys/jose-luis.\nYour public key has been saved in /home/jose-luis/.ssh/fimexKeys/jose-luis.pub.\nThe key fingerprint is:\nSHA256:a1nqbsh0Lbg+KmtRQquMw082Kvg6ZdpdtAsXtj0SSLM jose-luis\nThe key's randomart image is:\n+---[RSA 2048]----+\n|                 |\n|  . o            |\n| . o +           |\n|  o E =          |\n|+. o o BS..      |\n|+o++. O ==.      |\n|.*=o.* *=o       |\n|=.+.. *o.       

## Updating fabfile.py with credentials and ip

In [3]:
if (platform.system() == "Linux"):
    callPopen("sed -i s/^env\.hosts.*/env.hosts=\['{}']/ fabfile.py".format(ip))
    callPopen("sed -i s/^env\.user.*/env.user=\'{}\'/ fabfile.py".format(username))
    callPopen("sed -i s$^env\.key_filename.*$env\.key_filename='{}'$ fabfile.py".format(keyDir + '/' + username))
    callPopen("sed -i s/^env\.roledefs.*/env.roledefs={{\\'{}\\':[\\'{}\\'],/ fabfile.py".format('ncquery',ip))

fabfile = os.path.join("C:\\Users\\jose_luis_guerrero\\Envs\\mylai\\prognos_calibration","fabfile.py")
    
if (platform.system() == "Windows"):    
    replace(fabfile, "^env\.hosts.*",         "env.hosts=['{}']".format(ip))
    replace(fabfile, "^env\.user.*",          "env.user='{}'".format(username))
    replace(fabfile, "^env\.key_filename.*",  "env.key_filename='{}'".format(os.path.join(keyDir,username)))
    replace(fabfile, "^env\.roledefs.*",      "env.roledefs={{'{}':['{}'],".format('ncquery',ip))

#Testing connection
#Adding key to remote machine
time.sleep(2) #Giving time for the editing to work
if not instanceExists:
    p = Popen("ssh -i {0}/{1} {1}@{2} -o UserKnownHostsFile=/dev/null -o StrictHostKeyChecking=no".format(keyDir,username,ip),shell=True,stdout=PIPE,stdin=PIPE)
    print(p.communicate())

time.sleep(2)

sed -i s/^env\.hosts.*/env.hosts=\['35.234.102.160']/ fabfile.py
sed -i s/^env\.user.*/env.user='jose-luis'/ fabfile.py
sed -i s$^env\.key_filename.*$env\.key_filename='/home/jose-luis/.ssh/fimexKeys/jose-luis'$ fabfile.py
sed -i s/^env\.roledefs.*/env.roledefs={\'ncquery\':[\'35.234.102.160\'],/ fabfile.py
(b'', None)


## Setting fimex in the remote machine

In [6]:
if not instanceExists:
    callPopen('fab installDependencies')

fab installDependencies
[35.234.102.160] Executing task 'installDependencies'
[35.234.102.160] Executing task 'updateMachine'
[35.234.102.160] run: sudo apt-get update
[35.234.102.160] out: 
[35.234.102.160] out: 0% [Working]
[35.234.102.160] out:             
[35.234.102.160] out: Hit:1 http://europe-west3-a.gce.clouds.archive.ubuntu.com/ubuntu xenial InRelease
[35.234.102.160] out: 
[35.234.102.160] out: 0% [Waiting for headers] [Connecting to archive.canonical.com (91.189.92.191)]
[35.234.102.160] out:                                                                               
[35.234.102.160] out: Get:2 http://security.ubuntu.com/ubuntu xenial-security InRelease [107 kB]
[35.234.102.160] out: 
[35.234.102.160] out: 0% [Waiting for headers] [2 InRelease 12.6 kB/107 kB 12%] [Waiting for headers]
[35.234.102.160] out: 0% [1 InRelease gpgv 247 kB] [Waiting for headers] [2 InRelease 12.6 kB/107 kB 
[35.234.102.160] out:                                                                 

[35.234.102.160] out: 0% [8 Sources store 0 B] [5 InRelease gpgv 107 kB] [14 Packages 3,146 kB/7,532 
[35.234.102.160] out: 0% [8 Sources store 0 B] [5 InRelease gpgv 107 kB] [14 Packages 3,913 kB/7,532 
[35.234.102.160] out:                                                                                
[35.234.102.160] out: Get:18 http://security.ubuntu.com/ubuntu xenial-security/universe amd64 Packages [395 kB]
[35.234.102.160] out: 
[35.234.102.160] out: 0% [8 Sources store 0 B] [5 InRelease gpgv 107 kB] [14 Packages 4,962 kB/7,532 
[35.234.102.160] out: 0% [8 Sources store 0 B] [5 InRelease gpgv 107 kB] [14 Packages 5,374 kB/7,532 
[35.234.102.160] out:                                                                                
[35.234.102.160] out: Get:19 http://security.ubuntu.com/ubuntu xenial-security/universe Translation-en [152 kB]
[35.234.102.160] out: 
[35.234.102.160] out: 0% [8 Sources store 0 B] [5 InRelease gpgv 107 kB] [14 Packages 6,488 kB/7,532 
[35.234.102.160]

[35.234.102.160] out: 
[35.234.102.160] out: 93% [8 Sources store 0 B] [36 Sources 6,740 B/6,740 B 100%]
[35.234.102.160] out:                                                            
[35.234.102.160] out: 93% [8 Sources store 0 B]
[35.234.102.160] out:                          
[35.234.102.160] out: Get:37 http://europe-west3-a.gce.clouds.archive.ubuntu.com/ubuntu xenial-backports/main amd64 Packages [7,304 B]
[35.234.102.160] out: 
[35.234.102.160] out: 93% [8 Sources store 0 B] [37 Packages 7,304 B/7,304 B 100%]
[35.234.102.160] out:                                                             
[35.234.102.160] out: 93% [8 Sources store 0 B]
[35.234.102.160] out:                          
[35.234.102.160] out: Get:38 http://europe-west3-a.gce.clouds.archive.ubuntu.com/ubuntu xenial-backports/main Translation-en [4,456 B]
[35.234.102.160] out: 
[35.234.102.160] out: 93% [8 Sources store 0 B] [38 Translation-en 4,456 B/4,456 B 100%]
[35.234.102.160] out:                             

[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... Done
[35.234.102.160] out: 
[35.234.102.160] out: 

[35.234.102.160] Executing task 'installUtilities'
[35.234.102.160] run: yes | sudo apt-get install gcc g++ gfortran cmake make git libnetcdf-dev libnetcdff-dev netcdf-bin xmlstarlet tmux unzip python3-netcdf4 cdo
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 0%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 100%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... Done
[35.234.102.160] out: 
[35.234.102.160] out: 
[35.234.102.160] out: Building dependency tree... 0%
[35.234.102.160] out: 
[35.234.102.160] out: Building dependency tree... 0%
[35.234.102.160] out: 
[35.234.102.160] out: Building dependency tree... 50%
[35.234.102.160] out: 
[35.234.102.160] out: Building dependency tree... 50%
[35.234.102.160] out: 
[35.234.102.160] out: Building dependency tree       
[35.234.102.160] out: 
[35.234.102.

[35.234.102.160] out: 
[35.234.102.160] out: 1% [2 libarchive13 58.5 kB/262 kB 22%]
[35.234.102.160] out:                                       
[35.234.102.160] out: 1% [Working]
[35.234.102.160] out:             
[35.234.102.160] out: Get:3 http://europe-west3-a.gce.clouds.archive.ubuntu.com/ubuntu xenial/main amd64 libjsoncpp1 amd64 1.7.2-1 [73.0 kB]
[35.234.102.160] out: 
[35.234.102.160] out: 1% [3 libjsoncpp1 58.6 kB/73.0 kB 80%]
[35.234.102.160] out:                                       
[35.234.102.160] out: 1% [Working]
[35.234.102.160] out:             
[35.234.102.160] out: Get:4 http://europe-west3-a.gce.clouds.archive.ubuntu.com/ubuntu xenial-updates/main amd64 cmake amd64 3.5.1-1ubuntu3 [2,623 kB]
[35.234.102.160] out: 
[35.234.102.160] out: 1% [4 cmake 50.8 kB/2,623 kB 2%]
[35.234.102.160] out:                                 
[35.234.102.160] out: 2% [Waiting for headers]
[35.234.102.160] out:                         
[35.234.102.160] out: Get:5 http://europe-west3-a.g

...

[35.234.102.160] out: 
[35.234.102.160] out: Setting up libalgorithm-diff-xs-perl (0.04-4build1) ...
[35.234.102.160] out: 
[35.234.102.160] out: Setting up libalgorithm-merge-perl (0.08-3) ...
[35.234.102.160] out: 
[35.234.102.160] out: Setting up libblas-common (3.6.0-2ubuntu2) ...
[35.234.102.160] out: 
[35.234.102.160] out: Setting up libblas3 (3.6.0-2ubuntu2) ...
[35.234.102.160] out: 
[35.234.102.160] out: update-alternatives: using /usr/lib/libblas/libblas.so.3 to provide /usr/lib/libblas.so.3 (libblas.so.3) in auto mode
[35.234.102.160] out: 
[35.234.102.160] out: Setting up libcurl4-gnutls-dev:amd64 (7.47.0-1ubuntu2.11) ...
[35.234.102.160] out: 
[35.234.102.160] out: Setting up libfile-fcntllock-perl (0.22-3) ...
[35.234.102.160] out: 
[35.234.102.160] out: Setting up libhdf5-cpp-11:amd64 (1.8.16+docs-4ubuntu1.1) ...
[35.234.102.160] out: 
[35.234.102.160] out: Setting up zlib1g-dev:amd64 (1:1.2.8.dfsg-2ubuntu4.1) ...
[35.234.102.160] out: 
[35.234.102.160] out: Setting up l

[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 0%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 0%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 1%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 6%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 6%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 9%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 9%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 10%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 10%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 10%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 10%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 48%
[35.234.102.160] out: 
[35.234.102.160] out: Reading package lists... 48%
[35.234.102.160] out: 
[35.234.102.160] out: 

[35.234.102.160] out: 0% [Working]
[35.234.102.160] out:             
[35.234.102.160] out: Get:1 http://europe-west3-a.gce.clouds.archive.ubuntu.com/ubuntu xenial-updates/main amd64 icu-devtools amd64 55.1-7ubuntu0.4 [166 kB]
[35.234.102.160] out: 
[35.234.102.160] out: 0% [1 icu-devtools 12.6 kB/166 kB 8%] [Waiting for headers]
[35.234.102.160] out:                                                            
[35.234.102.160] out: 1% [Waiting for headers] [Waiting for headers]
[35.234.102.160] out:                                               
[35.234.102.160] out: Get:2 http://europe-west3-a.gce.clouds.archive.ubuntu.com/ubuntu xenial-updates/main amd64 libboost1.58-dev amd64 1.58.0+dfsg-5ubuntu3.1 [6,222 kB]
[35.234.102.160] out: 
[35.234.102.160] out: 1% [2 libboost1.58-dev 17.7 kB/6,222 kB 0%] [Waiting for headers]
[35.234.102.160] out:                                                                  
[35.234.102.160] out: Get:3 http://ppa.launchpad.net/met-norway/fimex/ubuntu xe

[35.234.102.160] out: 48% [18 fimex-0.66-dbg 7,468 B/21.5 MB 0%]
[35.234.102.160] out: 54% [18 fimex-0.66-dbg 3,197 kB/21.5 MB 15%]
[35.234.102.160] out: 60% [18 fimex-0.66-dbg 6,257 kB/21.5 MB 29%]
[35.234.102.160] out: 64% [18 fimex-0.66-dbg 8,148 kB/21.5 MB 38%]
[35.234.102.160] out: 67% [18 fimex-0.66-dbg 9,655 kB/21.5 MB 45%]
[35.234.102.160] out:                                             
[35.234.102.160] out: 69% [18 fimex-0.66-dbg 10.7 MB/21.5 MB 50%]
[35.234.102.160] out: 72% [18 fimex-0.66-dbg 12.3 MB/21.5 MB 57%]
[35.234.102.160] out: 75% [18 fimex-0.66-dbg 14.2 MB/21.5 MB 66%]
[35.234.102.160] out: 79% [18 fimex-0.66-dbg 16.1 MB/21.5 MB 75%]
[35.234.102.160] out: 81% [18 fimex-0.66-dbg 17.5 MB/21.5 MB 81%]
[35.234.102.160] out: 84% [18 fimex-0.66-dbg 19.0 MB/21.5 MB 88%]
[35.234.102.160] out: 87% [18 fimex-0.66-dbg 20.4 MB/21.5 MB 95%]
[35.234.102.160] out: 89% [18 fimex-0.66-dbg 21.5 MB/21.5 MB 100%]                      6,040 kB/s 0s
[35.234.102.160] out: 90% [Working] 

[35.234.102.160] out: Selecting previously unselected package libicu-dev:amd64.
[35.234.102.160] out: 
[35.234.102.160] out: Preparing to unpack .../libicu-dev_55.1-7ubuntu0.4_amd64.deb ...
[35.234.102.160] out: 
[35.234.102.160] out: Unpacking libicu-dev:amd64 (55.1-7ubuntu0.4) ...
[35.234.102.160] out: 
[35.234.102.160] out: Selecting previously unselected package liblog4cpp5v5.
[35.234.102.160] out: 
[35.234.102.160] out: Preparing to unpack .../liblog4cpp5v5_1.0-4.1_amd64.deb ...
[35.234.102.160] out: 
[35.234.102.160] out: Unpacking liblog4cpp5v5 (1.0-4.1) ...
[35.234.102.160] out: 
[35.234.102.160] out: Selecting previously unselected package libxml2-dev:amd64.
[35.234.102.160] out: 
[35.234.102.160] out: Preparing to unpack .../libxml2-dev_2.9.3+dfsg1-1ubuntu0.6_amd64.deb ...
[35.234.102.160] out: 
[35.234.102.160] out: Unpacking libxml2-dev:amd64 (2.9.3+dfsg1-1ubuntu0.6) ...
[35.234.102.160] out: 
[35.234.102.160] out: Selecting previously unselected package libfelt-0.66-0.
[35

## Querying extent of the basin
### Connecting to geodatabase

In [7]:
token = b'gAAAAABayyyn8ZnEstm8ZQqClUYQ-IqFFuMO4QTbmFJADHWBAcirh52s5stDwSwtVK7qVm5tzdTNFxTQjuRF28b1t2rosFSl_nnTowWrD4itOjkzF7s6Kg_qa1Adqpj59OAfBapgkToUQUHvEFY1Njc4he36AC76gmb8t0CJCq4ze2pDHWIlGdDacZxQ1jq14uLVxrFfCTSxDPX8Mx9W1av723etkOdWvw=='
key = getpass.getpass('Password: ')
credentials = decryptCredentials(token,key)

#Setting up credentials for google maps api access
apiToken = b'gAAAAABaXyLsGnF3ms4sC3ZhoLCwWAx9q0tydWl8XKEwOy8CO0W6Eqc8J4om8HNDlNR9nExYCmSrelp8W5R-PLtcce1I2UgW3YnlXXqWvrMN-outYwXhZoc59djfF752mzOPqXBHgpNC'
apiKey = decryptString(apiToken,key)
gmaps.configure(api_key=apiKey)

#print(credentials)

# Testing connection to database
try : 
    conn = db.connect("dbname={} user={} host={} password={}".format(credentials['database'],credentials['username'],credentials['host'],credentials['password']))
except :
    print("Unable to connect")
    
conn.close()  

Password: ········


### Querying catchment extent
The catchment must have been delineated beforehand

In [8]:
#box='BOX(10.680739923014 59.3434714764489,11.1305912803339 59.859034461037)' #Vanjsø
getBox=True
if getBox:
    basinSchema='basins'
    conn = db.connect("dbname={} user={} host={} password={}".format(credentials['database'],
                                                                           credentials['username'],
                                                                            credentials['host'],
                                                                            credentials['password']
                                                                          )
                           )
    #And a test query
    cursor = conn.cursor()

    cursor.execute('''SELECT ST_Extent(ST_Transform(ST_Buffer(a.basin,2000),4326)) FROM %(tableSHP)s AS a;'''
                      ,{"tableSHP": AsIs(basinSchema+'.resultsShp')}
                  )

    rows=cursor.fetchall()

#     for row in rows:
#         print(row[0])

    box=rows[0][0]
    
    conn.close()
box=box.replace(',',' ').replace(' ','\\\,')
print(box)

BOX(10.6455996902874\\,59.3254806900319\\,11.1657556268116\\,59.8770296312615)


## Getting list of openDAP links with high-resolution (1km2) temperature and precipitation data

In [ ]:
getFileList=False
baseURL='https://thredds.met.no/thredds/catalog/ngcd/version_18.09/catalog.html'
rain='RR/$'
temperature='TG'
model='type2'

only_a_tags = SoupStrainer("a", href=True)

def getSoup(url,re_str):
    request=requests.get(url)
    soup=BeautifulSoup(request.content,'lxml',parse_only=only_a_tags)
    link_soup=soup.find_all('a',text=re.compile(re_str))
    links=[]
    for i in link_soup:
        links.append(urljoin(url,i['href']))
    return links

if getFileList:
    allRainLinks=[]
    for var_link in getSoup(baseURL,rain):
        for model_link in getSoup(var_link,model):
            for year_link in getSoup(model_link,'^[0-9]{4}/$'):
                print('Processing {}'.format(year_link))
                for month_link in getSoup(year_link,'^[0-9]{2}/$'):
                    for day_link in getSoup(month_link,'\\.nc$'):
                        for opendap_link in getSoup(day_link,'^/thredds/dodsC/'):
                            allRainLinks.append(re.sub(r'\.html$', '', opendap_link))

    allTemperatureLinks=[]
    for var_link in getSoup(baseURL,temperature):
        for model_link in getSoup(var_link,model):
            for year_link in getSoup(model_link,'^[0-9]{4}/$'):
                print('Processing {}'.format(year_link))
                for month_link in getSoup(year_link,'^[0-9]{2}/$'):
                    for day_link in getSoup(month_link,'\\.nc$'):
                        for opendap_link in getSoup(day_link,'^/thredds/dodsC/'):
                            allTemperatureLinks.append(re.sub(r'\.html$', '', opendap_link))
                            
    with open('rain_nc_files.txt', 'w') as f:
        for item in allRainLinks:
            f.write("%s\n" % item)
    with open('temperature_nc_files.txt', 'w') as f:
        for item in allTemperatureLinks:
            f.write("%s\n" % item)    

These list of opendap links to netcdf files are then passed to a virtual machine containing the fimex utility in order to get data only for the basin of interest.

In [11]:
callPopen('''fab getDataForBasin:{},{},{},{},{} '''.format('rain_nc_files.txt',
                                                                       box,
                                                                       './rain_nc',
                                                                       'rain_vansjo.nc4',
                                                                        'RR')
         )
        

callPopen('''fab getDataForBasin:{},{},{},{},{} '''.format('temperature_nc_files.txt',
                                                                       box,
                                                                       './temperature_nc',
                                                                       'temperature_vansjo.nc4',
                                                                       'TG')
         )        

fab getDataForBasin:rain_nc_files.txt,BOX(10.6455996902874\\,59.3254806900319\\,11.1657556268116\\,59.8770296312615),./rain_nc,rain_vansjo.nc4,RR 
[35.234.102.160] Executing task 'getDataForBasin'
[35.234.102.160] Executing task 'getFromList'
[35.234.102.160] run: rm -rf ./rain_nc
[35.234.102.160] run: mkdir -p ./rain_nc
[35.234.102.160] put: rain_nc_files.txt -> ./rain_nc/rain_nc_files.txt
[35.234.102.160] put: getsubset.sh -> ./rain_nc/getsubset.sh
[35.234.102.160] run: cd ./rain_nc && chmod +x getsubset.sh && ./getsubset.sh 'rain_nc_files.txt' 'BOX(10.6455996902874\,59.3254806900319\,11.1657556268116\,59.8770296312615)' 'rain_vansjo.nc4' 'RR' 
[35.234.102.160] out: rain_nc_files.txt and BOX(10.6455996902874\,59.3254806900319\,11.1657556268116\,59.8770296312615) and rain_vansjo.nc4
[35.234.102.160] out: BOX(10.6455996902874\,59.3254806900319\,11.1657556268116\,59.8770296312615)
[35.234.102.160] out: The boundaries are:
[35.234.102.160] out: 10.6455996902874
[35.234.102.160] out: 59.3

[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring 

[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoringWARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out:  in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring 

[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: WARN: selected variable 'nv' does not exist, ign

[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: 240
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv'

...

[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoringWARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out:  in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring 

[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: 17200
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'n

[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoringWARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line  in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring 

[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring 

[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: selected variable 'nv' does not exist, ignoring in /build/fimex-0.66-eQyefp/fimex-0.66-0.66.0/src/CDMExtractor.cc at line 275
[35.234.102.160] out: WARN: selected variable 'nv' does not exist, ignoring 